 Fraud Data Analysis
Deep Dive into E-commerce Transaction Patterns

Objective: Explore fraud patterns in e-commerce data to identify risk factors.

Key Questions:
1. What time patterns indicate fraud?
2. Which browsers/devices are high-risk?
3. How does purchase behavior differ?
4. What are the geographic risk factors?

In [37]:
# Import libraries
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from datetime import datetime, timedelta
import warnings
warnings.filterwarnings('ignore')
import json
from pathlib import Path
import sys

# Custom styling
plt.style.use('seaborn-v0_8-darkgrid')
sns.set_palette("husl")
plt.rcParams['figure.figsize'] = (16, 10)

# Add src to path for custom modules
sys.path.append(str(Path.cwd().parent / "src"))

In [38]:
import pandas as pd
from pathlib import Path
import os

# Get the current working directory
current_dir = Path.cwd()
print(f"📁 Current working directory: {current_dir}")

# Go up one level to the root folder, then to data/processed
root_dir = current_dir.parent.parent  # Go up two levels from notebooks/Data_Anlysis_Processing/
processed_dir = root_dir / "data" / "processed"

print(f"📁 Looking for data in: {processed_dir.absolute()}")
print(f"📁 Directory exists: {processed_dir.exists()}")

if processed_dir.exists():
    # List ALL files
    print("\n📂 All files in processed directory:")
    all_files = list(processed_dir.iterdir())
    for i, file in enumerate(all_files, 1):
        file_size_mb = file.stat().st_size / (1024 * 1024)
        print(f"  {i:2}. {file.name} ({file_size_mb:.1f} MB)")
    
    # Look for fraud data files
    print("\n🔍 Searching for fraud data files...")
    fraud_files = []
    for file in all_files:
        file_lower = file.name.lower()
        if ('fraud' in file_lower or 'is_fraud' in file_lower) and file.suffix == '.csv':
            fraud_files.append(file)
    
    if fraud_files:
        print(f"✅ Found {len(fraud_files)} fraud-related files:")
        for file in fraud_files:
            print(f"  • {file.name}")
        
        # Filter for files with 'fraud_with_country' in name as they appear to be the most recent
        latest_fraud_files = [f for f in fraud_files if 'fraud_with_country' in f.name.lower()]
        
        if latest_fraud_files:
            # Get the most recent based on modification time
            latest_file = max(latest_fraud_files, key=lambda x: x.stat().st_mtime)
            print(f"\n🎯 Using most recent fraud data file: {latest_file.name}")
            fraud_file = latest_file
        else:
            # Use the first fraud file
            fraud_file = fraud_files[0]
            print(f"\n🎯 Using fraud data file: {fraud_file.name}")
        
        # Now load the file
        try:
            # First, check what columns the file has
            print("\n🔍 Checking file structure...")
            sample_df = pd.read_csv(fraud_file, nrows=5)
            print(f"Columns found: {list(sample_df.columns)}")
            
            # Identify date columns
            date_columns = []
            for col in sample_df.columns:
                if any(date_term in col.lower() for date_term in ['time', 'date', 'timestamp']):
                    date_columns.append(col)
            
            print(f"Date-like columns detected: {date_columns}")
            
            # Now load the full file with appropriate date parsing
            if date_columns:
                print(f"\n📥 Loading with date parsing for columns: {date_columns}")
                fraud_df = pd.read_csv(fraud_file, parse_dates=date_columns)
            else:
                print(f"\n📥 Loading without date parsing")
                fraud_df = pd.read_csv(fraud_file)
            
            print(f"✅ Successfully loaded: {fraud_df.shape[0]:,} rows, {fraud_df.shape[1]} columns")
            
            # Check for fraud indicator column
            print(f"\n🔎 Looking for fraud indicator column...")
            fraud_indicator_candidates = []
            for col in fraud_df.columns:
                col_lower = col.lower()
                if any(term in col_lower for term in ['class', 'fraud', 'is_fraud', 'label', 'target']):
                    fraud_indicator_candidates.append(col)
            
            if fraud_indicator_candidates:
                print(f"Possible fraud indicators: {fraud_indicator_candidates}")
                # Use the first one
                fraud_col = fraud_indicator_candidates[0]
                
                if fraud_df[fraud_col].nunique() == 2:
                    fraud_count = fraud_df[fraud_col].sum()
                    fraud_percentage = (fraud_count / len(fraud_df)) * 100
                    print(f"\n📊 Fraud statistics using '{fraud_col}':")
                    print(f"   • Total transactions: {len(fraud_df):,}")
                    print(f"   • Fraud cases: {fraud_count:,}")
                    print(f"   • Fraud percentage: {fraud_percentage:.4f}%")
                    
                    # Show distribution
                    print(f"\n📈 Distribution:")
                    print(fraud_df[fraud_col].value_counts().to_string())
                else:
                    print(f"⚠️ Column '{fraud_col}' has {fraud_df[fraud_col].nunique()} unique values")
            else:
                print("⚠️ No clear fraud indicator column found")
            
            # Display basic info
            print(f"\n📋 First 3 rows:")
            display(fraud_df.head(3))
            
            print(f"\n📊 Data types:")
            print(fraud_df.dtypes.head(20))
            
        except Exception as e:
            print(f"❌ Error loading file: {str(e)[:200]}")
            print("Trying alternative loading method...")
            
            # Try loading without parse_dates first
            try:
                fraud_df = pd.read_csv(fraud_file)
                print(f"✅ Loaded without date parsing: {fraud_df.shape[0]:,} rows")
                
                # Try to convert any date-like columns
                for col in fraud_df.columns:
                    if any(date_term in col.lower() for date_term in ['time', 'date', 'timestamp']):
                        try:
                            fraud_df[col] = pd.to_datetime(fraud_df[col])
                            print(f"✅ Converted '{col}' to datetime")
                        except:
                            print(f"⚠️ Could not convert '{col}' to datetime")
                
            except Exception as e2:
                print(f"❌ Failed to load: {e2}")
                # Create empty dataframe
                fraud_df = pd.DataFrame()
                
    else:
        print("❌ No fraud-related CSV files found")
        print("\n📋 Available CSV files:")
        csv_files = [f for f in all_files if f.suffix == '.csv']
        for file in csv_files[:10]:  # Show first 10
            print(f"  • {file.name}")
        
        # Try loading the first CSV file if available
        if csv_files:
            print(f"\n🔄 Trying to load first CSV file: {csv_files[0].name}")
            try:
                fraud_df = pd.read_csv(csv_files[0])
                print(f"✅ Loaded: {fraud_df.shape[0]:,} rows, {fraud_df.shape[1]} columns")
            except Exception as e:
                print(f"❌ Failed: {e}")
                fraud_df = pd.DataFrame()
        else:
            fraud_df = pd.DataFrame()
            
else:
    print("❌ Processed directory does not exist at the expected location!")
    print(f"Expected path: {processed_dir.absolute()}")
    print("\n🔍 Let me check alternative paths...")
    
    # Try different possible paths
    alternative_paths = [
        current_dir.parent / "data" / "processed",  # Go up one level from notebooks/
        Path("D:/10 acadamy/fraud-detection-ml-system/data/processed"),  # Absolute path
        Path("../data/processed"),  # Relative path
        Path("./data/processed"),   # Current directory
    ]
    
    for path in alternative_paths:
        print(f"\nChecking: {path.absolute()}")
        if path.exists():
            print(f"✅ Found directory!")
            processed_dir = path
            break
    
    if processed_dir.exists():
        print(f"\n✅ Using directory: {processed_dir.absolute()}")
        # List files
        all_files = list(processed_dir.iterdir())
        print(f"Found {len(all_files)} files")
        for file in all_files[:5]:
            print(f"  • {file.name}")
        
        # Look for any CSV file
        csv_files = [f for f in all_files if f.suffix == '.csv']
        if csv_files:
            print(f"\n📥 Loading first CSV file: {csv_files[0].name}")
            try:
                fraud_df = pd.read_csv(csv_files[0])
                print(f"✅ Loaded: {fraud_df.shape[0]:,} rows")
            except Exception as e:
                print(f"❌ Failed: {e}")
                fraud_df = pd.DataFrame()
        else:
            fraud_df = pd.DataFrame()
    else:
        print("\n❌ Could not find data directory anywhere!")
        print("Please check your project structure.")
        fraud_df = pd.DataFrame()

# If we successfully loaded data, show more info
if not fraud_df.empty:
    print(f"\n" + "="*80)
    print("✅ DATA LOADED SUCCESSFULLY!")
    print("="*80)
    print(f"📊 Shape: {fraud_df.shape[0]} rows × {fraud_df.shape[1]} columns")
    
    # Check data types
    date_cols = [col for col in fraud_df.columns if pd.api.types.is_datetime64_any_dtype(fraud_df[col])]
    numeric_cols = [col for col in fraud_df.columns if pd.api.types.is_numeric_dtype(fraud_df[col])]
    object_cols = [col for col in fraud_df.columns if fraud_df[col].dtype == 'object']
    
    print(f"📅 Date columns ({len(date_cols)}): {date_cols}")
    print(f"🔢 Numeric columns ({len(numeric_cols)}): {numeric_cols[:10]}{'...' if len(numeric_cols) > 10 else ''}")
    print(f"🔤 Object columns ({len(object_cols)}): {object_cols[:10]}{'...' if len(object_cols) > 10 else ''}")
    
    # Check for missing values
    missing = fraud_df.isnull().sum()
    if missing.sum() > 0:
        print(f"\n⚠️ Missing values found:")
        for col, count in missing[missing > 0].items():
            percentage = (count / len(fraud_df)) * 100
            print(f"  • {col}: {count:,} ({percentage:.1f}%)")
    else:
        print(f"\n✅ No missing values")
    print("="*80)
else:
    print("\n❌ No data was loaded. Please check your file paths.")

📁 Current working directory: d:\10 acadamy\fraud-detection-ml-system\notebooks\Data_Anlysis_Processing
📁 Looking for data in: d:\10 acadamy\fraud-detection-ml-system\data\processed
📁 Directory exists: True

📂 All files in processed directory:
   1. creditcard_cleaned.csv (143.6 MB)
   2. creditcard_cleaned_20251219_103703.csv (143.6 MB)
   3. creditcard_cleaned_20251221_110457.csv (143.6 MB)
   4. creditcard_data_processed_20251218_173255.csv (144.1 MB)
   5. creditcard_data_processed_latest.csv (144.1 MB)
   6. fraud_data_cleaned.csv (15.9 MB)
   7. fraud_data_cleaned_20251219_103703.csv (14.3 MB)
   8. fraud_data_cleaned_20251221_110457.csv (15.9 MB)
   9. fraud_data_processed_20251218_173255.csv (14.3 MB)
  10. fraud_data_processed_latest.csv (14.3 MB)
  11. fraud_with_country_20251219_123003.csv (15.2 MB)
  12. fraud_with_country_20251219_144637.csv (15.2 MB)
  13. fraud_with_country_20251219_152202.csv (15.9 MB)
  14. ip_country_data_processed_20251218_173255.csv (4.8 MB)
  15. ip

user_id         signup_time       purchase_time  purchase_value  \
0    22058 2015-02-24 22:55:49 2015-04-18 02:47:11              34   
1   333320 2015-06-07 20:39:50 2015-06-08 01:38:54              16   
2     1359 2015-01-01 18:52:44 2015-01-01 18:52:45              15   

       device_id source browser sex  age    ip_address  class        country  
0  QVPSPJUOCKZAR    SEO  Chrome   M   39  7.327584e+08      0          Japan  
1  EOGFQPIZPYXFZ    Ads  Chrome   F   53  3.503114e+08      0  United States  
2  YSSKYOSJHPPLJ    SEO   Opera   M   53  2.621474e+09      1  United States


📊 Data types:
user_id                    int64
signup_time       datetime64[ns]
purchase_time     datetime64[ns]
purchase_value             int64
device_id                 object
source                    object
browser                   object
sex                       object
age                        int64
ip_address               float64
class                      int64
country                   object
dtype: object

✅ DATA LOADED SUCCESSFULLY!
📊 Shape: 151112 rows × 12 columns
📅 Date columns (2): ['signup_time', 'purchase_time']
🔢 Numeric columns (5): ['user_id', 'purchase_value', 'age', 'ip_address', 'class']
🔤 Object columns (5): ['device_id', 'source', 'browser', 'sex', 'country']

✅ No missing values


In [39]:
# Create time-based features
if 'purchase_time' in fraud_df.columns:
    fraud_df['purchase_hour'] = fraud_df['purchase_time'].dt.hour
    fraud_df['purchase_day'] = fraud_df['purchase_time'].dt.day_name()
    fraud_df['purchase_month'] = fraud_df['purchase_time'].dt.month
    
if 'signup_time' in fraud_df.columns and 'purchase_time' in fraud_df.columns:
    fraud_df['time_since_signup_hours'] = (fraud_df['purchase_time'] - fraud_df['signup_time']).dt.total_seconds() / 3600
    fraud_df['is_immediate'] = (fraud_df['time_since_signup_hours'] < 1).astype(int)
    fraud_df['is_same_day'] = (fraud_df['time_since_signup_hours'] < 24).astype(int)

if 'purchase_hour' in fraud_df.columns:
    fraud_df['is_night'] = ((fraud_df['purchase_hour'] >= 0) & (fraud_df['purchase_hour'] < 6)).astype(int)
    fraud_df['is_weekend'] = fraud_df['purchase_time'].dt.dayofweek.isin([5, 6]).astype(int)

print("✅ Time features created successfully")

✅ Time features created successfully


In [40]:
# Create comprehensive time analysis dashboard
fig = make_subplots(
    rows=2, cols=3,
    subplot_titles=('Fraud Rate by Hour of Day', 
                    'Fraud Rate by Day of Week',
                    'Time Since Signup Distribution',
                    'Immediate Purchase Analysis',
                    'Night vs Day Fraud Comparison',
                    'Weekend vs Weekday Patterns'),
    specs=[[{'type': 'bar'}, {'type': 'bar'}, {'type': 'histogram'}],
           [{'type': 'pie'}, {'type': 'bar'}, {'type': 'bar'}]],
    vertical_spacing=0.12
)

# 1. Fraud Rate by Hour
if 'purchase_hour' in fraud_df.columns and 'class' in fraud_df.columns:
    hourly_stats = fraud_df.groupby('purchase_hour')['class'].agg(['count', 'sum'])
    hourly_stats['fraud_rate'] = (hourly_stats['sum'] / hourly_stats['count']) * 100
    
    fig.add_trace(
        go.Bar(x=hourly_stats.index, y=hourly_stats['fraud_rate'],
               marker_color='#E74C3C',
               name='Fraud Rate %'),
        row=1, col=1
    )
    
    # Add threshold line
    fig.add_hline(y=hourly_stats['fraud_rate'].mean(), line_dash="dash", 
                  line_color="red", row=1, col=1,
                  annotation_text=f"Avg: {hourly_stats['fraud_rate'].mean():.1f}%")

# 2. Fraud Rate by Day
if 'purchase_day' in fraud_df.columns and 'class' in fraud_df.columns:
    day_order = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']
    daily_stats = fraud_df.groupby('purchase_day')['class'].agg(['count', 'sum'])
    if not daily_stats.empty:
        daily_stats = daily_stats.reindex(day_order)
        daily_stats['fraud_rate'] = (daily_stats['sum'] / daily_stats['count']) * 100
        
        fig.add_trace(
            go.Bar(x=daily_stats.index, y=daily_stats['fraud_rate'],
                   marker_color='#3498DB',
                   name='Fraud Rate %'),
            row=1, col=2
        )

# 3. Time Since Signup Distribution
if 'time_since_signup_hours' in fraud_df.columns:
    fig.add_trace(
        go.Histogram(x=np.log1p(fraud_df['time_since_signup_hours']),
                     nbinsx=50,
                     marker_color='#9B59B6',
                     name='Time Since Signup (log)'),
        row=1, col=3
    )
    
    # Add fraud overlay
    if 'class' in fraud_df.columns:
        fraud_times = np.log1p(fraud_df[fraud_df['class'] == 1]['time_since_signup_hours'])
        fig.add_trace(
            go.Histogram(x=fraud_times,
                         nbinsx=50,
                         marker_color='#E74C3C',
                         opacity=0.7,
                         name='Fraud Cases'),
            row=1, col=3
        )

# 4. Immediate Purchase Analysis
if 'is_immediate' in fraud_df.columns and 'class' in fraud_df.columns:
    immediate_stats = fraud_df.groupby('is_immediate')['class'].agg(['count', 'sum'])
    immediate_stats['fraud_rate'] = (immediate_stats['sum'] / immediate_stats['count']) * 100
    
    fig.add_trace(
        go.Pie(labels=['Not Immediate', 'Immediate (<1 hour)'],
               values=immediate_stats['fraud_rate'].values,
               marker_colors=['#2ECC71', '#E74C3C'],
               textinfo='percent+label',
               hole=0.4),
        row=2, col=1
    )

# 5. Night vs Day Fraud
if 'is_night' in fraud_df.columns and 'class' in fraud_df.columns:
    night_stats = fraud_df.groupby('is_night')['class'].agg(['count', 'sum'])
    night_stats['fraud_rate'] = (night_stats['sum'] / night_stats['count']) * 100
    
    fig.add_trace(
        go.Bar(x=['Day (6AM-12AM)', 'Night (12AM-6AM)'],
               y=night_stats['fraud_rate'],
               marker_color=['#3498DB', '#2C3E50'],
               name='Fraud Rate'),
        row=2, col=2
    )

# 6. Weekend vs Weekday
if 'is_weekend' in fraud_df.columns and 'class' in fraud_df.columns:
    weekend_stats = fraud_df.groupby('is_weekend')['class'].agg(['count', 'sum'])
    weekend_stats['fraud_rate'] = (weekend_stats['sum'] / weekend_stats['count']) * 100
    
    fig.add_trace(
        go.Bar(x=['Weekday', 'Weekend'],
               y=weekend_stats['fraud_rate'],
               marker_color=['#F39C12', '#8E44AD'],
               name='Fraud Rate'),
        row=2, col=3
    )

# Update layout
fig.update_layout(height=900, 
                  showlegend=True,
                  title_text="🕒 Time Pattern Analysis - Fraud Detection Insights",
                  title_font_size=20)
fig.show()

In [41]:
print("="*80)
print("🚨 IMMEDIATE PURCHASE ANALYSIS (<1 hour after signup)")
print("="*80)

if 'is_immediate' in fraud_df.columns and 'class' in fraud_df.columns:
    immediate_df = fraud_df[fraud_df['is_immediate'] == 1]
    
    if len(immediate_df) > 0:
        print(f"Total immediate purchases: {len(immediate_df):,}")
        print(f"Immediate fraud cases: {immediate_df['class'].sum():,}")
        immediate_fraud_rate = immediate_df['class'].sum()/len(immediate_df)*100
        overall_fraud_rate = fraud_df['class'].sum()/len(fraud_df)*100 if 'class' in fraud_df.columns else 0
        print(f"Immediate fraud rate: {immediate_fraud_rate:.1f}%")
        print(f"vs Overall fraud rate: {overall_fraud_rate:.1f}%")
        
        print(f"\n📊 Immediate Purchase Statistics:")
        if 'purchase_value' in fraud_df.columns:
            print(f"  • Average purchase value: ${immediate_df['purchase_value'].mean():.2f}")
        
        if 'browser' in fraud_df.columns:
            browser_mode = immediate_df['browser'].mode()
            if not browser_mode.empty:
                print(f"  • Most common browser: {browser_mode.iloc[0]}")
        
        if 'source' in fraud_df.columns:
            source_mode = immediate_df['source'].mode()
            if not source_mode.empty:
                print(f"  • Most common source: {source_mode.iloc[0]}")
        
        print(f"\n🔍 Examples:")
        sample_immediate = immediate_df.head(3)
        for idx, row in sample_immediate.iterrows():
            fraud_flag = "🚩 FRAUD" if row['class'] == 1 else "✅ Legitimate"
            amount = f"Amount: ${row['purchase_value']:.2f}" if 'purchase_value' in row else "Amount: N/A"
            browser = f"Browser: {row['browser']}" if 'browser' in row else "Browser: N/A"
            time_diff = f"Time diff: {row['time_since_signup_hours']:.2f} hours" if 'time_since_signup_hours' in row else ""
            
            print(f"  User {row['user_id']}: {fraud_flag}, {amount}, {browser}, {time_diff}")
    else:
        print("No immediate purchases found (<1 hour after signup)")
else:
    print("Required columns not available for immediate purchase analysis")

🚨 IMMEDIATE PURCHASE ANALYSIS (<1 hour after signup)
Total immediate purchases: 7,641
Immediate fraud cases: 7,604
Immediate fraud rate: 99.5%
vs Overall fraud rate: 9.4%

📊 Immediate Purchase Statistics:
  • Average purchase value: $36.98
  • Most common browser: Chrome
  • Most common source: Ads

🔍 Examples:
  User 1359: 🚩 FRAUD, Amount: $15.00, Browser: Opera, Time diff: 0.00 hours
  User 171711: 🚩 FRAUD, Amount: $52.00, Browser: IE, Time diff: 0.00 hours
  User 151705: 🚩 FRAUD, Amount: $48.00, Browser: Chrome, Time diff: 0.00 hours


In [42]:
# Create browser analysis dashboard
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=('Fraud Rate by Browser',
                    'Transaction Volume by Browser',
                    'Browser-Source Combination Risk',
                    'Device Usage Patterns'),
    specs=[[{'type': 'bar'}, {'type': 'bar'}],
           [{'type': 'heatmap'}, {'type': 'box'}]],
    vertical_spacing=0.15
)

# 1. Fraud Rate by Browser
if 'browser' in fraud_df.columns and 'class' in fraud_df.columns:
    browser_stats = fraud_df.groupby('browser')['class'].agg(['count', 'sum'])
    browser_stats['fraud_rate'] = (browser_stats['sum'] / browser_stats['count']) * 100
    browser_stats = browser_stats.sort_values('fraud_rate', ascending=False)
    
    fig.add_trace(
        go.Bar(x=browser_stats.index, y=browser_stats['fraud_rate'],
               marker_color='#E74C3C',
               text=browser_stats['fraud_rate'].round(1),
               textposition='auto'),
        row=1, col=1
    )
    
    # 2. Transaction Volume by Browser
    fig.add_trace(
        go.Bar(x=browser_stats.index, y=browser_stats['count'],
               marker_color='#3498DB',
               text=[f"{x:,}" for x in browser_stats['count']],
               textposition='auto'),
        row=1, col=2
    )

# 3. Browser-Source Heatmap
if 'browser' in fraud_df.columns and 'source' in fraud_df.columns and 'class' in fraud_df.columns:
    try:
        browser_source_matrix = fraud_df.pivot_table(
            index='browser', 
            columns='source', 
            values='class', 
            aggfunc='mean'
        ) * 100
        
        if not browser_source_matrix.empty:
            fig.add_trace(
                go.Heatmap(z=browser_source_matrix.values,
                           x=browser_source_matrix.columns,
                           y=browser_source_matrix.index,
                           colorscale='Reds',
                           colorbar=dict(title="Fraud Rate %")),
                row=2, col=1
            )
    except Exception as e:
        print(f"Note: Could not create browser-source heatmap: {e}")

# 4. Device Analysis
if 'device_id' in fraud_df.columns and 'user_id' in fraud_df.columns:
    device_user_counts = fraud_df.groupby('device_id')['user_id'].nunique()
    multi_user_devices = device_user_counts[device_user_counts > 1]
    
    if len(multi_user_devices) > 0:
        fig.add_trace(
            go.Box(y=multi_user_devices.values,
                   name='Users per Device',
                   marker_color='#9B59B6',
                   boxmean=True),
            row=2, col=2
        )

fig.update_layout(height=800,
                  title_text="🌐 Browser & Device Risk Analysis",
                  title_font_size=20)
fig.show()

In [43]:
print("="*80)
print("🌐 CRITICAL BROWSER INSIGHTS")
print("="*80)

if 'browser' in fraud_df.columns and 'class' in fraud_df.columns:
    browser_stats = fraud_df.groupby('browser')['class'].agg(['count', 'sum'])
    browser_stats['fraud_rate'] = (browser_stats['sum'] / browser_stats['count']) * 100
    
    # Top 3 high-risk browsers
    avg_fraud_rate = browser_stats['fraud_rate'].mean()
    high_risk_browsers = browser_stats[browser_stats['fraud_rate'] > avg_fraud_rate].head(3)
    
    if not high_risk_browsers.empty:
        print("\n🚨 HIGH-RISK BROWSERS (Above Average Fraud Rate):")
        for browser, row in high_risk_browsers.iterrows():
            print(f"  • {browser}: {row['fraud_rate']:.1f}% fraud rate "
                  f"({int(row['sum']):,} fraud cases out of {int(row['count']):,} transactions)")
    
    # Device sharing analysis
    if 'device_id' in fraud_df.columns and 'user_id' in fraud_df.columns:
        device_user_counts = fraud_df.groupby('device_id')['user_id'].nunique()
        multi_user_devices = device_user_counts[device_user_counts > 1]
        
        print(f"\n🔍 DEVICE SHARING ANALYSIS:")
        print(f"  • Devices used by multiple users: {len(multi_user_devices):,}")
        
        # Fixed: Properly handle empty case for max
        max_users = device_user_counts.max() if len(device_user_counts) > 0 else 0
        print(f"  • Max users per device: {max_users}")
        
        # Fixed: Properly handle empty case for mean with conditional formatting
        if len(device_user_counts) > 0:
            avg_users = device_user_counts.mean()
            print(f"  • Average users per device: {avg_users:.2f}")
        else:
            print(f"  • Average users per device: 0")
        
        # Flag suspicious devices
        suspicious_devices = device_user_counts[device_user_counts > 5]
        if len(suspicious_devices) > 0:
            print(f"  ⚠️  Suspicious devices (>5 users): {len(suspicious_devices)}")
            for device_id, user_count in suspicious_devices.head(3).items():
                device_data = fraud_df[fraud_df['device_id'] == device_id]
                if 'class' in device_data.columns:
                    device_fraud_rate = device_data['class'].mean() * 100
                else:
                    device_fraud_rate = 0
                print(f"     Device {device_id[:8]}...: {user_count} users, {device_fraud_rate:.1f}% fraud")
else:
    print("Required columns not available for browser analysis")

🌐 CRITICAL BROWSER INSIGHTS

🚨 HIGH-RISK BROWSERS (Above Average Fraud Rate):
  • Chrome: 9.9% fraud rate (6,069 fraud cases out of 61,432 transactions)
  • FireFox: 9.5% fraud rate (2,342 fraud cases out of 24,610 transactions)

🔍 DEVICE SHARING ANALYSIS:
  • Devices used by multiple users: 6,175
  • Max users per device: 20
  • Average users per device: 1.10
  ⚠️  Suspicious devices (>5 users): 741
     Device AAAXXOZJ...: 11 users, 90.9% fraud
     Device AANYBGQS...: 8 users, 87.5% fraud
     Device ADEDUDCY...: 14 users, 92.9% fraud


In [44]:
# Create purchase analysis dashboard
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=('Purchase Value Distribution',
                    'Fraud vs Legitimate Amounts',
                    'Amount vs Time Since Signup',
                    'Purchase Value Risk Bands'),
    specs=[[{'type': 'histogram'}, {'type': 'box'}],
           [{'type': 'scatter'}, {'type': 'bar'}]],
    vertical_spacing=0.15
)

# 1. Purchase Value Distribution
if 'purchase_value' in fraud_df.columns:
    fig.add_trace(
        go.Histogram(x=np.log1p(fraud_df['purchase_value']),
                     nbinsx=50,
                     marker_color='#3498DB',
                     name='All Transactions'),
        row=1, col=1
    )
    
    # Add fraud overlay
    if 'class' in fraud_df.columns:
        fraud_amounts = np.log1p(fraud_df[fraud_df['class'] == 1]['purchase_value'])
        fig.add_trace(
            go.Histogram(x=fraud_amounts,
                         nbinsx=50,
                         marker_color='#E74C3C',
                         opacity=0.7,
                         name='Fraud Cases'),
            row=1, col=1
        )

# 2. Box plot comparison
if 'purchase_value' in fraud_df.columns and 'class' in fraud_df.columns:
    legit_amounts = fraud_df[fraud_df['class'] == 0]['purchase_value'].dropna()
    fraud_amounts_box = fraud_df[fraud_df['class'] == 1]['purchase_value'].dropna()
    
    if len(legit_amounts) > 0:
        fig.add_trace(
            go.Box(y=legit_amounts,
                   name='Legitimate',
                   marker_color='#2ECC71',
                   boxmean=True),
            row=1, col=2
        )
    
    if len(fraud_amounts_box) > 0:
        fig.add_trace(
            go.Box(y=fraud_amounts_box,
                   name='Fraud',
                   marker_color='#E74C3C',
                   boxmean=True),
            row=1, col=2
        )

# 3. Scatter: Amount vs Time Since Signup
if 'time_since_signup_hours' in fraud_df.columns and 'purchase_value' in fraud_df.columns and 'class' in fraud_df.columns:
    fig.add_trace(
        go.Scatter(x=fraud_df['time_since_signup_hours'],
                   y=fraud_df['purchase_value'],
                   mode='markers',
                   marker=dict(
                       size=8,
                       color=fraud_df['class'],
                       colorscale=['#2ECC71', '#E74C3C'],
                       showscale=True,
                       colorbar=dict(
                           title=dict(text="Fraud", side="top")  # Correct syntax
                       )
                   ),
                   name='Amount vs Time'),
        row=2, col=1
    )

# 4. Risk bands analysis
if 'purchase_value' in fraud_df.columns and 'class' in fraud_df.columns:
    amount_bins = [0, 10, 20, 50, 100, 200, 500, 1000, float('inf')]
    amount_labels = ['<$10', '$10-20', '$20-50', '$50-100', 
                     '$100-200', '$200-500', '$500-1000', '>$1000']
    
    fraud_df['amount_band'] = pd.cut(fraud_df['purchase_value'], 
                                    bins=amount_bins, 
                                    labels=amount_labels)
    
    band_stats = fraud_df.groupby('amount_band')['class'].agg(['count', 'sum'])
    band_stats['fraud_rate'] = (band_stats['sum'] / band_stats['count']) * 100
    
    fig.add_trace(
        go.Bar(x=band_stats.index, y=band_stats['fraud_rate'],
               marker_color='#9B59B6',
               text=band_stats['fraud_rate'].round(1),
               textposition='auto'),
        row=2, col=2
    )

fig.update_layout(height=800,
                  title_text="💰 Purchase Behavior Analysis",
                  title_font_size=20)
fig.show()

In [45]:
print("="*80)
print("💰 PURCHASE BEHAVIOR INSIGHTS")
print("="*80)

if 'purchase_value' in fraud_df.columns:
    print(f"\n📊 OVERALL STATISTICS:")
    print(f"  • Average purchase: ${fraud_df['purchase_value'].mean():.2f}")
    print(f"  • Median purchase: ${fraud_df['purchase_value'].median():.2f}")
    print(f"  • Std deviation: ${fraud_df['purchase_value'].std():.2f}")
    print(f"  • Max purchase: ${fraud_df['purchase_value'].max():.2f}")
    print(f"  • Min purchase: ${fraud_df['purchase_value'].min():.2f}")

# Fraud vs Legitimate comparison
if 'purchase_value' in fraud_df.columns and 'class' in fraud_df.columns:
    fraud_stats = fraud_df[fraud_df['class'] == 1]['purchase_value'].describe()
    legit_stats = fraud_df[fraud_df['class'] == 0]['purchase_value'].describe()
    
    print(f"\n🔍 FRAUD VS LEGITIMATE COMPARISON:")
    print(f"  • Fraud avg: ${fraud_stats['mean']:.2f} vs Legitimate avg: ${legit_stats['mean']:.2f}")
    print(f"  • Fraud median: ${fraud_stats['50%']:.2f} vs Legitimate median: ${legit_stats['50%']:.2f}")
    print(f"  • Fraud std: ${fraud_stats['std']:.2f} vs Legitimate std: ${legit_stats['std']:.2f}")

# Risk bands analysis
if 'amount_band' in fraud_df.columns:
    band_stats = fraud_df.groupby('amount_band')['class'].agg(['count', 'sum'])
    band_stats['fraud_rate'] = (band_stats['sum'] / band_stats['count']) * 100
    
    print(f"\n🎯 RISK BANDS ANALYSIS:")
    if not band_stats['fraud_rate'].empty:
        max_band = band_stats['fraud_rate'].idxmax()
        min_band = band_stats['fraud_rate'].idxmin()
        print(f"  • Highest fraud rate: {max_band} ({band_stats['fraud_rate'].max():.1f}%)")
        print(f"  • Lowest fraud rate: {min_band} ({band_stats['fraud_rate'].min():.1f}%)")

💰 PURCHASE BEHAVIOR INSIGHTS

📊 OVERALL STATISTICS:
  • Average purchase: $36.94
  • Median purchase: $35.00
  • Std deviation: $18.32
  • Max purchase: $154.00
  • Min purchase: $9.00

🔍 FRAUD VS LEGITIMATE COMPARISON:
  • Fraud avg: $36.99 vs Legitimate avg: $36.93
  • Fraud median: $35.00 vs Legitimate median: $35.00
  • Fraud std: $18.40 vs Legitimate std: $18.32

🎯 RISK BANDS ANALYSIS:
  • Highest fraud rate: <$10 (9.8%)
  • Lowest fraud rate: $100-200 (3.6%)


In [46]:
# Create demographics dashboard
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=('Age Distribution',
                    'Fraud Rate by Age Group',
                    'Gender Distribution',
                    'Age-Gender Fraud Matrix'),
    specs=[[{'type': 'histogram'}, {'type': 'bar'}],
           [{'type': 'pie'}, {'type': 'heatmap'}]],
    vertical_spacing=0.15
)

# 1. Age Distribution
if 'age' in fraud_df.columns:
    fig.add_trace(
        go.Histogram(x=fraud_df['age'],
                     nbinsx=30,
                     marker_color='#3498DB',
                     name='All Users'),
        row=1, col=1
    )
    
    # Add fraud overlay
    if 'class' in fraud_df.columns:
        fraud_ages = fraud_df[fraud_df['class'] == 1]['age']
        fig.add_trace(
            go.Histogram(x=fraud_ages,
                         nbinsx=30,
                         marker_color='#E74C3C',
                         opacity=0.7,
                         name='Fraud Cases'),
            row=1, col=1
        )

# 2. Fraud Rate by Age Group
if 'age' in fraud_df.columns and 'class' in fraud_df.columns:
    age_bins = [18, 25, 35, 45, 55, 65, 100]
    age_labels = ['18-25', '26-35', '36-45', '46-55', '56-65', '65+']
    
    fraud_df['age_group'] = pd.cut(fraud_df['age'], 
                                  bins=age_bins, 
                                  labels=age_labels)
    
    age_stats = fraud_df.groupby('age_group')['class'].agg(['count', 'sum'])
    age_stats['fraud_rate'] = (age_stats['sum'] / age_stats['count']) * 100
    
    fig.add_trace(
        go.Bar(x=age_stats.index, y=age_stats['fraud_rate'],
               marker_color='#9B59B6',
               text=age_stats['fraud_rate'].round(1),
               textposition='auto'),
        row=1, col=2
    )

# 3. Gender Distribution
if 'sex' in fraud_df.columns:
    gender_stats = fraud_df['sex'].value_counts()
    fig.add_trace(
        go.Pie(labels=gender_stats.index,
               values=gender_stats.values,
               marker_colors=['#3498DB', '#9B59B6'],
               hole=0.4),
        row=2, col=1
    )

# 4. Age-Gender Fraud Matrix
if 'age_group' in fraud_df.columns and 'sex' in fraud_df.columns and 'class' in fraud_df.columns:
    try:
        age_gender_matrix = fraud_df.pivot_table(
            index='age_group', 
            columns='sex', 
            values='class', 
            aggfunc='mean'
        ) * 100
        
        if not age_gender_matrix.empty:
            fig.add_trace(
                go.Heatmap(z=age_gender_matrix.values,
                           x=age_gender_matrix.columns,
                           y=age_gender_matrix.index,
                           colorscale='Reds',
                           colorbar=dict(title="Fraud Rate %")),
                row=2, col=2
            )
    except Exception as e:
        print(f"Note: Could not create age-gender heatmap: {e}")

fig.update_layout(height=800,
                  title_text="👥 User Demographics Analysis",
                  title_font_size=20)
fig.show()

In [47]:
print("="*80)
print("👥 DEMOGRAPHICS INSIGHTS")
print("="*80)

# Age insights
if 'age' in fraud_df.columns:
    print(f"\n📊 AGE ANALYSIS:")
    print(f"  • Average age: {fraud_df['age'].mean():.1f} years")
    print(f"  • Age range: {fraud_df['age'].min()} to {fraud_df['age'].max()} years")
    print(f"  • Age std: {fraud_df['age'].std():.1f} years")

# High-risk age groups
if 'age_group' in fraud_df.columns and 'class' in fraud_df.columns:
    age_stats = fraud_df.groupby('age_group')['class'].agg(['count', 'sum'])
    age_stats['fraud_rate'] = (age_stats['sum'] / age_stats['count']) * 100
    
    print(f"\n🎯 HIGH-RISK AGE GROUPS:")
    avg_fraud_rate = age_stats['fraud_rate'].mean()
    for age_group in age_stats.index:
        fraud_rate = age_stats.loc[age_group, 'fraud_rate']
        if fraud_rate > avg_fraud_rate:
            print(f"  • {age_group}: {fraud_rate:.1f}% fraud rate "
                  f"({int(age_stats.loc[age_group, 'sum']):,} cases)")

# Gender insights
if 'sex' in fraud_df.columns and 'class' in fraud_df.columns:
    gender_fraud_stats = fraud_df.groupby('sex')['class'].agg(['count', 'sum'])
    gender_fraud_stats['fraud_rate'] = (gender_fraud_stats['sum'] / gender_fraud_stats['count']) * 100
    
    print(f"\n🚻 GENDER ANALYSIS:")
    for gender in ['M', 'F']:
        if gender in gender_fraud_stats.index:
            stats = gender_fraud_stats.loc[gender]
            print(f"  • {gender}: {stats['fraud_rate']:.1f}% fraud rate "
                  f"({int(stats['sum']):,} cases out of {int(stats['count']):,})")

👥 DEMOGRAPHICS INSIGHTS

📊 AGE ANALYSIS:
  • Average age: 33.1 years
  • Age range: 18 to 76 years
  • Age std: 8.6 years

🎯 HIGH-RISK AGE GROUPS:
  • 18-25: 9.0% fraud rate (2,582 cases)
  • 26-35: 9.3% fraud rate (5,838 cases)
  • 36-45: 9.7% fraud rate (4,246 cases)
  • 46-55: 9.2% fraud rate (1,082 cases)
  • 56-65: 10.0% fraud rate (131 cases)

🚻 GENDER ANALYSIS:
  • M: 9.6% fraud rate (8,434 cases out of 88,293)
  • F: 9.1% fraud rate (5,717 cases out of 62,819)


In [48]:
# Select numerical features for correlation
numerical_features = []
if 'purchase_value' in fraud_df.columns: numerical_features.append('purchase_value')
if 'age' in fraud_df.columns: numerical_features.append('age')
if 'time_since_signup_hours' in fraud_df.columns: numerical_features.append('time_since_signup_hours')
if 'purchase_hour' in fraud_df.columns: numerical_features.append('purchase_hour')
if 'class' in fraud_df.columns: numerical_features.append('class')

if len(numerical_features) >= 2:
    # Calculate correlation matrix
    corr_matrix = fraud_df[numerical_features].corr()
    
    # Create correlation heatmap
    fig = go.Figure(data=go.Heatmap(
        z=corr_matrix.values,
        x=corr_matrix.columns,
        y=corr_matrix.index,
        colorscale='RdBu',
        zmid=0,
        text=corr_matrix.round(2).values,
        texttemplate='%{text}',
        textfont={"size": 10}
    ))
    
    fig.update_layout(
        title='📊 Correlation Matrix - Numerical Features',
        title_font_size=20,
        height=600,
        xaxis_title="Features",
        yaxis_title="Features"
    )
    
    fig.show()
    
    # Feature correlation insights
    print("="*80)
    print("📊 FEATURE CORRELATION INSIGHTS")
    print("="*80)
    
    if 'class' in corr_matrix.columns:
        # Top correlations with fraud
        fraud_correlations = corr_matrix['class'].sort_values(ascending=False)
        
        print(f"\n🔗 TOP CORRELATIONS WITH FRAUD:")
        for feature, correlation in fraud_correlations.items():
            if feature != 'class' and abs(correlation) > 0.05:
                direction = "positively" if correlation > 0 else "negatively"
                print(f"  • {feature}: {correlation:.3f} ({direction} correlated)")
        
        # Critical finding
        if 'time_since_signup_hours' in corr_matrix.index:
            correlation_value = corr_matrix.loc['time_since_signup_hours', 'class']
            print(f"\n🚨 CRITICAL FINDING FROM CORRELATION ANALYSIS:")
            print(f"  • time_since_signup_hours has correlation of {correlation_value:.3f}")
            if correlation_value < -0.1:
                print(f"  • This confirms: Fraud happens QUICKLY after signup!")
else:
    print("Not enough numerical features for correlation analysis")

📊 FEATURE CORRELATION INSIGHTS

🔗 TOP CORRELATIONS WITH FRAUD:
  • time_since_signup_hours: -0.258 (negatively correlated)

🚨 CRITICAL FINDING FROM CORRELATION ANALYSIS:
  • time_since_signup_hours has correlation of -0.258
  • This confirms: Fraud happens QUICKLY after signup!


In [49]:
# Create output directories
output_base = Path("outputs/Data_Analysis_Processing")
reports_dir = output_base / "reports"
statistics_dir = output_base / "statistics"
visualizations_dir = output_base / "visualizations"

# Create all directories
for directory in [reports_dir, statistics_dir, visualizations_dir]:
    directory.mkdir(parents=True, exist_ok=True)

# Create comprehensive insights dictionary
eda_insights = {
    'timestamp': pd.Timestamp.now().isoformat(),
    'dataset_statistics': {
        'total_transactions': len(fraud_df),
        'fraud_count': fraud_df['class'].sum() if 'class' in fraud_df.columns else 0,
        'fraud_percentage': (fraud_df['class'].sum() / len(fraud_df) * 100) if 'class' in fraud_df.columns else 0,
        'unique_users': fraud_df['user_id'].nunique() if 'user_id' in fraud_df.columns else 0,
        'unique_devices': fraud_df['device_id'].nunique() if 'device_id' in fraud_df.columns else 0,
        'time_period': {}
    }
}

# Add time period if available
if 'purchase_time' in fraud_df.columns:
    eda_insights['dataset_statistics']['time_period'] = {
        'start': fraud_df['purchase_time'].min().isoformat(),
        'end': fraud_df['purchase_time'].max().isoformat(),
        'duration_days': (fraud_df['purchase_time'].max() - fraud_df['purchase_time'].min()).days
    }

# Add time patterns
if 'purchase_hour' in fraud_df.columns and 'class' in fraud_df.columns:
    hourly_stats = fraud_df.groupby('purchase_hour')['class'].agg(['count', 'sum'])
    hourly_stats['fraud_rate'] = (hourly_stats['sum'] / hourly_stats['count']) * 100
    eda_insights['time_patterns'] = {
        'hourly_fraud_rates': hourly_stats['fraud_rate'].to_dict()
    }

# Add immediate purchase analysis
if 'is_immediate' in fraud_df.columns and 'class' in fraud_df.columns:
    immediate_df = fraud_df[fraud_df['is_immediate'] == 1]
    eda_insights['time_patterns']['immediate_purchase_analysis'] = {
        'count': len(immediate_df),
        'fraud_count': immediate_df['class'].sum(),
        'fraud_rate': (immediate_df['class'].sum() / len(immediate_df) * 100) if len(immediate_df) > 0 else 0
    }

# Add browser analysis
if 'browser' in fraud_df.columns and 'class' in fraud_df.columns:
    browser_stats = fraud_df.groupby('browser')['class'].agg(['count', 'sum'])
    browser_stats['fraud_rate'] = (browser_stats['sum'] / browser_stats['count']) * 100
    eda_insights['browser_analysis'] = {
        'browser_fraud_rates': browser_stats['fraud_rate'].to_dict()
    }

# Save insights
with open(reports_dir / "fraud_data_eda_insights.json", 'w') as f:
    json.dump(eda_insights, f, indent=4, default=str)

print("✅ EDA completed successfully!")
print(f"📁 Reports saved to: {reports_dir}")
print(f"📁 Statistics saved to: {statistics_dir}")
print(f"📁 Visualizations saved to: {visualizations_dir}")

# List saved files
print("\n📄 Saved files:")
for file in reports_dir.glob("*.json"):
    print(f"  • {file.name}")

✅ EDA completed successfully!
📁 Reports saved to: outputs\Data_Analysis_Processing\reports
📁 Statistics saved to: outputs\Data_Analysis_Processing\statistics
📁 Visualizations saved to: outputs\Data_Analysis_Processing\visualizations

📄 Saved files:
  • fraud_data_eda_insights.json
